In [1]:
newtype MCont r a = MCont { (>>-) :: (a -> r) -> r }

:t (>>-)

instance Functor (MCont r) where
    fmap f cra = MCont $ \k -> cra >>- \a -> k (f a)
    
instance Applicative (MCont r) where
    pure a = MCont $ \aTor -> aTor a
    cf <*> cx = MCont $ \bTor ->
        cx >>- \a ->
        cf >>- \f ->
        bTor (f a)
        
instance Monad (MCont r) where
    return = pure
    cra >>= f = MCont $ \bTor ->
        cra >>- \a ->
        (f a) >>- \b ->
        bTor b
        
join' :: MCont r (MCont r a) -> MCont r a
join' ccx = MCont $ \k ->
    ccx >>- \cx -> -- extract inner continuation
    cx >>- \x ->   -- extract value of inner continuation
    k x            -- wrap value in k again

(>>-) :: forall r a. MCont r a -> (a -> r) -> r

In [2]:
square :: Int -> MCont r Int
square x = MCont $ \k -> k (x ^ 2)

add :: Int -> Int -> MCont r Int
add x y = MCont $ \k -> k (x + y)

In [8]:
pythagoras :: Int -> Int -> MCont r Int
pythagoras x y = do
    xsquare <- square x
    ysquare <- square y
    add xsquare ysquare